## 本番データで料理分類器を作ってみる

In [78]:
import pandas as pd
# from io import StringIO

# """https://stackoverflow.com/questions/19611729/getting-google-spreadsheet-csv-into-a-pandas-dataframe
# """
# import requests
# url = 'https://docs.google.com/spreadsheets/d/1a4fkAJNessYsmscETtugik3VtDf2fNzdToTeAUuhrYA/export?format=csv&id=cuisine'
# data = requests.get(url).content
# pd.read_csv(StringIO(data))
# pd.read_csv('https://docs.google.com/spreadsheets/d/1a4fkAJNessYsmscETtugik3VtDf2fNzdToTeAUuhrYA/export?format=csv')

cuisine_df = pd.read_csv('chefgohan.tsv', sep='\t').drop(['who'], axis=1).set_index('cuisine').query('is_standard == True').fillna('')
cuisine_df.head()

genre purpose hotorcold        taste       materials  \
cuisine                                                            
親子丼      japanese    main       hot  salty,sweet       rice,meat   
玉子焼き     japanese    side       hot  salty,sweet                   
鶏のから揚げ   japanese    side       hot        salty            meat   
肉じゃが     japanese    side       hot  saily,sweet  meat,vegetable   
天ぷら      japanese    side       hot        salty  fish,vegetable   

                 when               color  is_standard  \
cuisine                                                  
親子丼      lunch,dinner  yellow,green,white         True   
玉子焼き        breakfast              yellow         True   
鶏のから揚げ   lunch,dinner               brown         True   
肉じゃが           dinner     brown,green,red         True   
天ぷら      lunch,dinner    yellow,red,green         True   

                                                       url  
cuisine                                                     
親子丼      https://c-chefgohan.gnst.jp/imgdata/recipe/89/...  
玉子焼き     https://c-chefgohan.gnst.jp/imgdata/recipe/90/...  
鶏のから揚げ   https://c-chefgohan.gnst.jp/imgdata/recipe/91/...  
肉じゃが     https://c-chefgohan.gnst.jp/imgdata/recipe/95/...  
天ぷら      https://c-chefgohan.gnst.jp/imgdata/recipe/96/...

In [2]:
# import pandas as pd

# cuisine = [
#     {
#        'name': 'remen',
#         'genre': 'chinese',
#         'taste': ['spicy'],
#         'hotorcold': 'cold',
#     },
#     {
#        'name': 'baconeggs',
#         'genre': 'western',
#         'taste': ['salty'],
#         'hotorcold': 'hot',
#     },
#     {
#        'name': 'ebichili',
#         'genre': 'chinese',
#         'taste': ['spicy'],
#         'hotorcold': 'hot',
#     },
#     {
#        'name': 'oyakodon',
#         'genre': 'japanese',
#         'taste': ['salty', 'sweety'],
#         'hotorcold': 'hot',
#     },
# ]
# cuisine_df = pd.DataFrame(cuisine)
# cuisine_df.set_index('name')

genre hotorcold            taste
name                                          
remen       chinese      cold          [spicy]
baconeggs   western       hot          [salty]
ebichili    chinese       hot          [spicy]
oyakodon   japanese       hot  [salty, sweety]

### 料理データで決定木

### Preprocessing

In [85]:
"""nameの分類をしたいので、name以外のカラムを数値化していく（学習させるため）
カテゴリ変数->数値化は基本的にlabelbinarizerでok...
と思いきや決定系はnumericかbinarizeがいいようだ
https://medium.com/data-design/visiting-categorical-features-and-encoding-in-decision-trees-53400fa65931
"""

print(cuisine_df.columns)

cuisine_df.tail()

Index(['genre', 'purpose', 'hotorcold', 'taste', 'materials', 'when', 'color',
       'is_standard', 'url', 'parsed_when', 'parsed_color'],
      dtype='object')


genre  purpose hotorcold        taste materials  \
cuisine                                                            
チョコチップクッキー     western  dessert      cold        sweet             
イチゴのレアチーズケーキ   western  dessert      cold   sweet,sour             
アップルパイ         western  dessert      cold   sweet,sour             
みたらし団子        japanese  dessert      cold  sweet,salty             
イチゴのショートケーキ    western  dessert      cold   sweet,sour             

                      when             color  is_standard  \
cuisine                                                     
チョコチップクッキー           snack       black,brown         True   
イチゴのレアチーズケーキ         snack         white,red         True   
アップルパイ               snack         brown,red         True   
みたらし団子               snack       brown,white         True   
イチゴのショートケーキ   snack,dinner  white,red,yellow         True   

                                                            url   parsed_when  \
cuisine                                                                         
チョコチップクッキー    https://c-chefgohan.gnst.jp/imgdata/recipe/22/...         snack   
イチゴのレアチーズケーキ  https://c-chefgohan.gnst.jp/imgdata/recipe/69/...         snack   
アップルパイ        https://c-chefgohan.gnst.jp/imgdata/recipe/66/...         snack   
みたらし団子        https://c-chefgohan.gnst.jp/imgdata/recipe/55/...         snack   
イチゴのショートケーキ   https://c-chefgohan.gnst.jp/imgdata/recipe/77/...  dinner,snack   

                  parsed_color  
cuisine                         
チョコチップクッキー         black,brown  
イチゴのレアチーズケーキ         red,white  
アップルパイ               brown,red  
みたらし団子             brown,white  
イチゴのショートケーキ   red,white,yellow

### genre

In [28]:
cuisine_df.genre.unique()

array(['japanese', 'western', 'chinese', 'french', 'italian', 'spanish',
       'asian'], dtype=object)

In [30]:
from sklearn.preprocessing import LabelEncoder
le_genre = LabelEncoder()
labeled_genre = le_genre.fit_transform(cuisine_df.genre)
labeled_genre, le_genre.inverse_transform(labeled_genre)

(array([4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
        4, 4, 4, 4, 4, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2, 2, 3, 3, 3, 3, 5,
        5, 0, 0, 0, 0, 1, 6, 6, 6, 6, 4, 6]),
 array(['japanese', 'japanese', 'japanese', 'japanese', 'japanese',
        'japanese', 'japanese', 'japanese', 'japanese', 'japanese',
        'japanese', 'japanese', 'japanese', 'japanese', 'japanese',
        'japanese', 'japanese', 'japanese', 'japanese', 'japanese',
        'japanese', 'japanese', 'japanese', 'japanese', 'japanese',
        'japanese', 'japanese', 'japanese', 'western', 'western', 'western',
        'western', 'western', 'western', 'western', 'western', 'western',
        'western', 'western', 'western', 'western', 'chinese', 'chinese',
        'chinese', 'chinese', 'chinese', 'chinese', 'chinese', 'chinese',
        'chinese', 'chinese', 'chinese', 'chinese', 'chinese', 'chinese',
        'c

### purpose

In [63]:
from sklearn.preprocessing import LabelEncoder
le_purpose = LabelEncoder()
labeled_purpose = le_purpose.fit_transform(cuisine_df.purpose)
labeled_purpose, le_purpose.inverse_transform(labeled_purpose)

(array([1, 2, 2, 2, 2, 2, 2, 1, 1, 1, 2, 2, 2, 2, 2, 1, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 1, 1, 3, 1, 2, 2, 2, 2, 2, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 1,
        2, 1, 2, 2, 1, 2, 2, 2, 2, 1, 2, 2, 2, 2, 2, 2, 2, 2, 1, 1, 2, 1, 1,
        2, 1, 2, 2, 2, 0, 0, 0, 0, 0, 0, 0]),
 array(['main', 'side', 'side', 'side', 'side', 'side', 'side', 'main',
        'main', 'main', 'side', 'side', 'side', 'side', 'side', 'main',
        'side', 'side', 'side', 'side', 'side', 'side', 'side', 'side',
        'side', 'main', 'main', 'sidle', 'main', 'side', 'side', 'side',
        'side', 'side', 'main', 'main', 'main', 'side', 'side', 'side',
        'side', 'side', 'side', 'side', 'side', 'main', 'side', 'main',
        'side', 'side', 'main', 'side', 'side', 'side', 'side', 'main',
        'side', 'side', 'side', 'side', 'side', 'side', 'side', 'side',
        'main', 'main', 'side', 'main', 'main', 'side', 'main', 'side',
        'side', 'side', 'dessert', 'dessert', 'dessert', 'dessert',
      

### hot or cold

In [31]:
le_hotorcold = LabelEncoder()
labeled_hotorcold = le_hotorcold.fit_transform(cuisine_df.hotorcold)
labeled_hotorcold, le_hotorcold.inverse_transform(labeled_hotorcold)

(array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1,
        1, 1, 1, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]),
 array(['hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot',
        'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot',
        'cold', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot',
        'cold', 'hot', 'hot', 'cold', 'cold', 'hot', 'hot', 'hot', 'hot',
        'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot',
        'hot', 'hot', 'hot', 'hot', 'cold', 'cold', 'hot', 'hot', 'hot',
        'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'cold',
        'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot', 'hot',
        'cold', 'cold', 'cold', 'cold', 'cold', 'cold', 'cold', 'cold',
        'cold'], dtype=object))

### taste

In [49]:
l = ['x', 'o', 'r']
sorted(l)

['o', 'r', 'x']

In [73]:
"""str -> array; column: taste 
順番だけ整列させて文字列に戻す
"""
cuisine_df['parsed_taste'] = cuisine_df.taste.apply(lambda t: sorted(t.split(','))).apply(','.join)
cuisine_df.taste.head(), cuisine_df.parsed_taste.head()

(cuisine
 親子丼       salty,sweet
 玉子焼き      salty,sweet
 鶏のから揚げ          salty
 肉じゃが      saily,sweet
 天ぷら             salty
 Name: taste, dtype: object, cuisine
 親子丼       salty,sweet
 玉子焼き      salty,sweet
 鶏のから揚げ          salty
 肉じゃが      saily,sweet
 天ぷら             salty
 Name: parsed_taste, dtype: object)

In [74]:
"""このカラムは配列なのでMultiLaberBinalizerでないといけない
...と思いきや決定木なので以下でnumericにやってみる
"""
# from sklearn.preprocessing import MultiLabelBinarizer
# lb_taste = MultiLabelBinarizer()
# labeled_taste = lb_taste.fit_transform(cuisine_df.taste.values)
# labeled_taste, lb_taste.inverse_transform(labeled_taste)

le_taste = LabelEncoder()
labeled_taste = le_taste.fit_transform(cuisine_df.parsed_taste)
labeled_taste, le_taste.inverse_transform(labeled_taste)

(array([ 8,  8,  4,  3,  4,  6,  8,  4,  0,  4, 14,  8,  8,  8,  4, 14,  8,
         8,  1, 14,  4,  4, 10,  8,  8,  4,  8,  4,  8,  4,  8,  2,  8,  4,
         8,  6,  6,  8,  8,  4,  6,  7,  8,  5,  8,  6,  4,  6, 14, 11, 11,
         4,  4, 12,  8,  4, 12,  6,  6,  8,  4,  6,  9, 12,  6,  8,  4,  6,
         4,  6, 12, 10, 12, 13, 14, 14, 14, 11, 11,  8, 11]),
 array(['salty,sweet', 'salty,sweet', 'salty', 'saily,sweet', 'salty',
        'salty,spicy', 'salty,sweet', 'salty', 'bitter,daily,salty',
        'salty', 'sweet', 'salty,sweet', 'salty,sweet', 'salty,sweet',
        'salty', 'sweet', 'salty,sweet', 'salty,sweet',
        'bitter,salty,sweet', 'sweet', 'salty', 'salty', 'sour,spicy',
        'salty,sweet', 'salty,sweet', 'salty', 'salty,sweet', 'salty',
        'salty,sweet', 'salty', 'salty,sweet', 'saily,sour,spicy,sweet',
        'salty,sweet', 'salty', 'salty,sweet', 'salty,spicy', 'salty,spicy',
        'salty,sweet', 'salty,sweet', 'salty', 'salty,spicy',
        'salt

### materials

In [75]:
"""str -> array; column: taste 
順番だけ整列させて文字列に戻す
"""
cuisine_df['parsed_materials'] = cuisine_df.materials.apply(lambda t: sorted(t.split(','))).apply(','.join)
cuisine_df.materials.head(), cuisine_df.parsed_materials.head()

(cuisine
 親子丼            rice,meat
 玉子焼き                    
 鶏のから揚げ              meat
 肉じゃが      meat,vegetable
 天ぷら       fish,vegetable
 Name: materials, dtype: object, cuisine
 親子丼            meat,rice
 玉子焼き                    
 鶏のから揚げ              meat
 肉じゃが      meat,vegetable
 天ぷら       fish,vegetable
 Name: parsed_materials, dtype: object)

In [76]:
"""このカラムは配列なのでMultiLaberBinalizerでないといけない
...と思いきや決定木なので以下でnumericにやってみる
"""
le_materials = LabelEncoder()
labeled_materials = le_materials.fit_transform(cuisine_df.parsed_materials)
labeled_materials, le_materials.inverse_transform(labeled_materials)

(array([ 5,  0,  4,  6,  3, 14,  4, 12, 12, 14,  6,  0,  3,  1,  4,  5, 15,
        14, 15,  1,  7,  4,  3,  1,  0,  0,  0, 14,  4,  1,  4, 14,  0,  7,
         9, 12,  4,  0, 14,  4,  4,  1,  8,  0, 14, 12,  6,  9,  4,  6, 10,
         0,  0,  4,  6, 11,  4, 15, 14,  1,  8, 14, 14,  1,  9,  9,  3, 12,
         2,  1,  1,  3, 14, 13,  0,  0,  0,  0,  0,  0,  0]),
 array(['meat,rice', '', 'meat', 'meat,vegetable', 'fish,vegetable',
        'vegetable', 'meat', 'rice', 'rice', 'vegetable', 'meat,vegetable',
        '', 'fish,vegetable', 'fish', 'meat', 'meat,rice', 'vegetable ',
        'vegetable', 'vegetable ', 'fish', 'meat,vegetable ', 'meat',
        'fish,vegetable', 'fish', '', '', '', 'vegetable', 'meat', 'fish',
        'meat', 'vegetable', '', 'meat,vegetable ', 'noodle', 'rice',
        'meat', '', 'vegetable', 'meat', 'meat', 'fish', 'meet', '',
        'vegetable', 'rice', 'meat,vegetable', 'noodle', 'meat',
        'meat,vegetable', 'noodle,vegetable', '', '', 'meat',
     

### when

In [80]:
"""str -> array; column: taste 
順番だけ整列させて文字列に戻す
"""

cuisine_df['parsed_when'] = cuisine_df.when.apply(lambda t: sorted(t.split(','))).apply(','.join)
cuisine_df.when.head(), cuisine_df.parsed_when.head()

(cuisine
 親子丼       lunch,dinner
 玉子焼き         breakfast
 鶏のから揚げ    lunch,dinner
 肉じゃが            dinner
 天ぷら       lunch,dinner
 Name: when, dtype: object, cuisine
 親子丼       dinner,lunch
 玉子焼き         breakfast
 鶏のから揚げ    dinner,lunch
 肉じゃが            dinner
 天ぷら       dinner,lunch
 Name: parsed_when, dtype: object)

In [81]:
"""もしかしたらMultiLaberBinalizerのほうがいいかもしれない
"""
le_when = LabelEncoder()
labeled_when = le_when.fit_transform(cuisine_df.parsed_when)
labeled_when, le_when.inverse_transform(labeled_when)

(array([5, 0, 5, 3, 5, 5, 3, 3, 3, 3, 5, 1, 3, 5, 5, 5, 3, 3, 1, 5, 3, 5, 5,
        5, 3, 5, 5, 5, 5, 5, 3, 5, 5, 3, 5, 5, 5, 3, 3, 6, 6, 5, 3, 5, 5, 5,
        4, 4, 4, 5, 5, 5, 2, 5, 5, 4, 5, 5, 5, 5, 3, 3, 2, 3, 5, 5, 3, 5, 5,
        3, 3, 5, 3, 5, 7, 7, 7, 7, 7, 7, 6]),
 array(['dinner,lunch', 'breakfast', 'dinner,lunch', 'dinner',
        'dinner,lunch', 'dinner,lunch', 'dinner', 'dinner', 'dinner',
        'dinner', 'dinner,lunch', 'breakfast,dinner', 'dinner',
        'dinner,lunch', 'dinner,lunch', 'dinner,lunch', 'dinner', 'dinner',
        'breakfast,dinner', 'dinner,lunch', 'dinner', 'dinner,lunch',
        'dinner,lunch', 'dinner,lunch', 'dinner', 'dinner,lunch',
        'dinner,lunch', 'dinner,lunch', 'dinner,lunch', 'dinner,lunch',
        'dinner', 'dinner,lunch', 'dinner,lunch', 'dinner', 'dinner,lunch',
        'dinner,lunch', 'dinner,lunch', 'dinner', 'dinner', 'dinner,snack',
        'dinner,snack', 'dinner,lunch', 'dinner', 'dinner,lunch',
        'dinner,lunch', 

### color

In [83]:
"""str -> array; column: taste 
順番だけ整列させて文字列に戻す
"""

cuisine_df['parsed_color'] = cuisine_df.color.apply(lambda t: sorted(t.split(','))).apply(','.join)
cuisine_df.color.head(), cuisine_df.parsed_color.head()

(cuisine
 親子丼       yellow,green,white
 玉子焼き                  yellow
 鶏のから揚げ                 brown
 肉じゃが         brown,green,red
 天ぷら         yellow,red,green
 Name: color, dtype: object, cuisine
 親子丼       green,white,yellow
 玉子焼き                  yellow
 鶏のから揚げ                 brown
 肉じゃが         brown,green,red
 天ぷら         green,red,yellow
 Name: parsed_color, dtype: object)

In [84]:
"""もしかしたらMultiLaberBinalizerのほうがいいかもしれない
"""
le_color = LabelEncoder()
labeled_color = le_color.fit_transform(cuisine_df.parsed_color)
labeled_color, le_color.inverse_transform(labeled_color)

(array([19, 29,  2,  4, 18,  2,  2, 10, 29, 10,  5,  1,  2, 11,  2,  8, 10,
         6,  3,  2,  7,  2, 13, 28, 10,  9,  2, 27, 26,  7,  7, 17, 27,  3,
        14, 21,  4, 10, 10,  2,  2, 23,  4, 20, 20,  9,  6, 17,  2, 16, 18,
         2, 28,  8,  3,  9,  7,  7, 10, 27,  0, 18, 19, 23, 26, 22, 12, 27,
        26, 26, 24, 15, 23, 16, 27, 27,  1, 24,  7, 10, 25]),
 array(['green,white,yellow', 'yellow', 'brown', 'brown,green,red',
        'green,red,yellow', 'brown', 'brown', 'brown,white', 'yellow',
        'brown,white', 'brown,green,red,white', 'black,brown', 'brown',
        'brown,yellow', 'brown', 'brown,red,white', 'brown,white',
        'brown,green,yellow', 'brown,green', 'brown', 'brown,red', 'brown',
        'gray,green,red,yellow', 'white,yellow', 'brown,white',
        'brown,red,yellow', 'brown', 'white', 'red,yellow', 'brown,red',
        'brown,red', 'green,red,white,yellow', 'white', 'brown,green',
        'green,orange', 'pink,white', 'brown,green,red', 'brown,white',


### name

In [59]:
"""最後に目的変数の料理名をID化
"""
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
y = le.fit_transform(cuisine_df.index)
y, le.inverse_transform(y)

(array([69, 63, 75, 67, 55,  4, 76, 48, 66,  1,  7,  9, 38,  6, 64, 62,  5,
         2, 10, 24, 71, 77, 74, 68, 56, 19,  3, 54, 20, 18, 46, 40, 41, 47,
        31, 17, 30, 22, 25, 43, 36, 16, 72,  0,  8, 27, 73, 53, 70, 59, 50,
        57, 51, 80, 52, 61, 78, 79, 49, 42, 35, 44, 26, 37, 39, 23, 12, 45,
        32, 60, 34, 29, 21, 65, 58, 33, 28, 15, 13, 11, 14]),
 array(['親子丼', '玉子焼き', '鶏のから揚げ', '肉じゃが', '天ぷら', 'きんぴら', '鶏の照り焼き',
        '五目炊き込みごはん', '筍ごはん', 'おでん', 'すき焼き', 'ひじきの煮物', 'ブリ大根', 'さばの味噌煮',
        '生姜焼き', '牛丼', 'さといもの煮ころがし', 'かぼちゃの煮物', 'ほうれん草のごまあえ', 'カレイの煮付け',
        '豚汁', '鶏の竜田揚げ', '鯵の南蛮漬け', '西京焼き', '揚げ出し豆腐', 'エビ天そば', 'きつねそば',
        '大根サラダ', 'オムライス', 'エビフライ', 'ローストビーフ', 'ポテトサラダ', 'マカロニグラタン',
        'ロールキャベツ', 'ナポリタン', 'エビピラフ', 'ドライカレー', 'カニクリームコロッケ', 'クリームシチュー',
        'メンチカツ', 'フライドチキン', 'エビチリ', '酢豚', 'あんかけ かに玉', 'にらたま', 'チャーハン',
        '青椒肉絲（チンジャオロース）', '坦々麺', '豚の角煮', '棒々鶏 （バンバンジー)', '冷やし中華', '春巻き',
        '卵スープ', '麻婆豆腐', '回鍋肉 （ホイコーロー）', '焼きそば', '麻婆春雨', '麻婆茄子', '八宝菜'

## concatenate labeled data

In [104]:
import numpy as np

X = np.concatenate((
    labeled_genre.reshape(-1, 1),
    labeled_purpose.reshape(-1, 1),
    labeled_hotorcold.reshape(-1, 1),
    labeled_taste.reshape(-1, 1),
    labeled_materials.reshape(-1, 1),
    labeled_when.reshape(-1, 1),
    labeled_color.reshape(-1, 1),
), axis=1)
X, y

(array([[ 4,  1,  1,  8,  5,  5, 19],
        [ 4,  2,  1,  8,  0,  0, 29],
        [ 4,  2,  1,  4,  4,  5,  2],
        [ 4,  2,  1,  3,  6,  3,  4],
        [ 4,  2,  1,  4,  3,  5, 18],
        [ 4,  2,  1,  6, 14,  5,  2],
        [ 4,  2,  1,  8,  4,  3,  2],
        [ 4,  1,  1,  4, 12,  3, 10],
        [ 4,  1,  1,  0, 12,  3, 29],
        [ 4,  1,  1,  4, 14,  3, 10],
        [ 4,  2,  1, 14,  6,  5,  5],
        [ 4,  2,  1,  8,  0,  1,  1],
        [ 4,  2,  1,  8,  3,  3,  2],
        [ 4,  2,  1,  8,  1,  5, 11],
        [ 4,  2,  1,  4,  4,  5,  2],
        [ 4,  1,  1, 14,  5,  5,  8],
        [ 4,  2,  1,  8, 15,  3, 10],
        [ 4,  2,  1,  8, 14,  3,  6],
        [ 4,  2,  0,  1, 15,  1,  3],
        [ 4,  2,  1, 14,  1,  5,  2],
        [ 4,  2,  1,  4,  7,  3,  7],
        [ 4,  2,  1,  4,  4,  5,  2],
        [ 4,  2,  1, 10,  3,  5, 13],
        [ 4,  2,  1,  8,  1,  5, 28],
        [ 4,  2,  1,  8,  0,  3, 10],
        [ 4,  1,  1,  4,  0,  5,  9],
        [ 4,

## Training

In [105]:
from sklearn.tree import DecisionTreeClassifier, export_graphviz

model = DecisionTreeClassifier()
model.fit(X, y)

DecisionTreeClassifier(class_weight=None, criterion='gini', max_depth=None,
            max_features=None, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, presort=False, random_state=None,
            splitter='best')

In [106]:
def create_feature_name(column_name):
    """カラム名->数値化したカラム名に変換
    """
    labels = eval('lb_{}'.format(column_name)).classes_
    if len(labels) <= 2:
        return ['{}__'.format(column_name)]
    else:
        return ['{}__{}'.format(column_name, label) for label in labels]

create_feature_name('genre') #,　create_feature_name('hotorcold')

['genre__asian',
 'genre__chinese',
 'genre__french',
 'genre__italian',
 'genre__japanese',
 'genre__spanish',
 'genre__western']

In [108]:
from itertools import chain

def flatten(l):
    return list(chain.from_iterable(l))

def create_feature_columns():
#     return flatten([create_feature_name(name) for name in ['genre', 'hotorcold', 'taste']])
    return flatten([create_feature_name(name) for name in ['genre', 'taste']])

create_feature_columns()

['genre__asian',
 'genre__chinese',
 'genre__french',
 'genre__italian',
 'genre__japanese',
 'genre__spanish',
 'genre__western',
 'taste__bitter',
 'taste__daily',
 'taste__saily',
 'taste__salty',
 'taste__sour',
 'taste__spicy',
 'taste__sweet']

In [109]:
%matplotlib inline
from sklearn.externals.six import StringIO
from IPython.display import Image
import pydot_ng

dot_data = StringIO()
export_graphviz(model, 
                out_file=dot_data, 
#                 feature_names=create_feature_columns(),
                feature_names=['genre', 'purpose', 'hotorcold', 'taste', 'materials', 'when', 'color'],
                class_names=le.inverse_transform(y),
                filled=True,
                rounded=True,
                proportion=True,
               )
graph = pydot_ng.graph_from_dot_data(dot_data.getvalue())
Image(graph.create_png())

In [121]:
genre_dict = pd.DataFrame({
    'id': labeled_genre,
    'name': le_genre.inverse_transform(labeled_genre),
}).drop_duplicates().to_dict(orient='records')
genre_dict

[{'id': 4, 'name': 'japanese'},
 {'id': 6, 'name': 'western'},
 {'id': 1, 'name': 'chinese'},
 {'id': 2, 'name': 'french'},
 {'id': 3, 'name': 'italian'},
 {'id': 5, 'name': 'spanish'},
 {'id': 0, 'name': 'asian'}]

In [122]:
purpose_dict = pd.DataFrame({
    'id': labeled_purpose,
    'name': le_purpose.inverse_transform(labeled_purpose),
}).drop_duplicates().to_dict(orient='records')
purpose_dict

[{'id': 1, 'name': 'main'},
 {'id': 2, 'name': 'side'},
 {'id': 3, 'name': 'sidle'},
 {'id': 0, 'name': 'dessert'}]

In [123]:
hotorcold_dict = pd.DataFrame({
    'id': labeled_hotorcold,
    'name': le_hotorcold.inverse_transform(labeled_hotorcold),
}).drop_duplicates().to_dict(orient='records')
hotorcold_dict

[{'id': 1, 'name': 'hot'}, {'id': 0, 'name': 'cold'}]

In [124]:
taste_dict = pd.DataFrame({
    'id': labeled_taste,
    'name': le_taste.inverse_transform(labeled_taste),
}).drop_duplicates().to_dict(orient='records')
taste_dict

[{'id': 8, 'name': 'salty,sweet'},
 {'id': 4, 'name': 'salty'},
 {'id': 3, 'name': 'saily,sweet'},
 {'id': 6, 'name': 'salty,spicy'},
 {'id': 0, 'name': 'bitter,daily,salty'},
 {'id': 14, 'name': 'sweet'},
 {'id': 1, 'name': 'bitter,salty,sweet'},
 {'id': 10, 'name': 'sour,spicy'},
 {'id': 2, 'name': 'saily,sour,spicy,sweet'},
 {'id': 7, 'name': 'salty,spicy,sweet'},
 {'id': 5, 'name': 'salty,sour,sweet'},
 {'id': 11, 'name': 'sour,sweet'},
 {'id': 12, 'name': 'spicy'},
 {'id': 9, 'name': 'sour'},
 {'id': 13, 'name': 'spicy,sweet'}]

In [125]:
materials_dict = pd.DataFrame({
    'id': labeled_materials,
    'name': le_materials.inverse_transform(labeled_materials),
}).drop_duplicates().to_dict(orient='records')
materials_dict

[{'id': 5, 'name': 'meat,rice'},
 {'id': 0, 'name': ''},
 {'id': 4, 'name': 'meat'},
 {'id': 6, 'name': 'meat,vegetable'},
 {'id': 3, 'name': 'fish,vegetable'},
 {'id': 14, 'name': 'vegetable'},
 {'id': 12, 'name': 'rice'},
 {'id': 1, 'name': 'fish'},
 {'id': 15, 'name': 'vegetable '},
 {'id': 7, 'name': 'meat,vegetable '},
 {'id': 9, 'name': 'noodle'},
 {'id': 8, 'name': 'meet'},
 {'id': 10, 'name': 'noodle,vegetable'},
 {'id': 11, 'name': 'noodle,vegetable '},
 {'id': 2, 'name': 'fish,rice'},
 {'id': 13, 'name': 'rice,vegetable'}]

In [126]:
when_dict = pd.DataFrame({
    'id': labeled_when,
    'name': le_when.inverse_transform(labeled_when),
}).drop_duplicates().to_dict(orient='records')
when_dict

[{'id': 5, 'name': 'dinner,lunch'},
 {'id': 0, 'name': 'breakfast'},
 {'id': 3, 'name': 'dinner'},
 {'id': 1, 'name': 'breakfast,dinner'},
 {'id': 6, 'name': 'dinner,snack'},
 {'id': 4, 'name': 'dinner ,lunch'},
 {'id': 2, 'name': 'breakfast,dinner,lunch'},
 {'id': 7, 'name': 'snack'}]

In [128]:
y_dict = pd.DataFrame({
    'id': y,
    'name': le.inverse_transform(y),
}).drop_duplicates().to_dict(orient='records')
y_dict

[{'id': 69, 'name': '親子丼'},
 {'id': 63, 'name': '玉子焼き'},
 {'id': 75, 'name': '鶏のから揚げ'},
 {'id': 67, 'name': '肉じゃが'},
 {'id': 55, 'name': '天ぷら'},
 {'id': 4, 'name': 'きんぴら'},
 {'id': 76, 'name': '鶏の照り焼き'},
 {'id': 48, 'name': '五目炊き込みごはん'},
 {'id': 66, 'name': '筍ごはん'},
 {'id': 1, 'name': 'おでん'},
 {'id': 7, 'name': 'すき焼き'},
 {'id': 9, 'name': 'ひじきの煮物'},
 {'id': 38, 'name': 'ブリ大根'},
 {'id': 6, 'name': 'さばの味噌煮'},
 {'id': 64, 'name': '生姜焼き'},
 {'id': 62, 'name': '牛丼'},
 {'id': 5, 'name': 'さといもの煮ころがし'},
 {'id': 2, 'name': 'かぼちゃの煮物'},
 {'id': 10, 'name': 'ほうれん草のごまあえ'},
 {'id': 24, 'name': 'カレイの煮付け'},
 {'id': 71, 'name': '豚汁'},
 {'id': 77, 'name': '鶏の竜田揚げ'},
 {'id': 74, 'name': '鯵の南蛮漬け'},
 {'id': 68, 'name': '西京焼き'},
 {'id': 56, 'name': '揚げ出し豆腐'},
 {'id': 19, 'name': 'エビ天そば'},
 {'id': 3, 'name': 'きつねそば'},
 {'id': 54, 'name': '大根サラダ'},
 {'id': 20, 'name': 'オムライス'},
 {'id': 18, 'name': 'エビフライ'},
 {'id': 46, 'name': 'ローストビーフ'},
 {'id': 40, 'name': 'ポテトサラダ'},
 {'id': 41, 'name': 'マカロニグラタン'},
 {'id':

In [ ]:
y_dict = pd.DataFrame({
    'id': labeled_color,
    'name': le_color.inverse_transform(labeled_color),
}).drop_duplicates().to_dict(orient='records')
color_dict

In [129]:
genre_dict, purpose_dict, hotorcold_dict, taste_dict, materials_dict, when_dict, color_dict, y_dict

([{'id': 4, 'name': 'japanese'},
  {'id': 6, 'name': 'western'},
  {'id': 1, 'name': 'chinese'},
  {'id': 2, 'name': 'french'},
  {'id': 3, 'name': 'italian'},
  {'id': 5, 'name': 'spanish'},
  {'id': 0, 'name': 'asian'}],
 [{'id': 1, 'name': 'main'},
  {'id': 2, 'name': 'side'},
  {'id': 3, 'name': 'sidle'},
  {'id': 0, 'name': 'dessert'}],
 [{'id': 1, 'name': 'hot'}, {'id': 0, 'name': 'cold'}],
 [{'id': 8, 'name': 'salty,sweet'},
  {'id': 4, 'name': 'salty'},
  {'id': 3, 'name': 'saily,sweet'},
  {'id': 6, 'name': 'salty,spicy'},
  {'id': 0, 'name': 'bitter,daily,salty'},
  {'id': 14, 'name': 'sweet'},
  {'id': 1, 'name': 'bitter,salty,sweet'},
  {'id': 10, 'name': 'sour,spicy'},
  {'id': 2, 'name': 'saily,sour,spicy,sweet'},
  {'id': 7, 'name': 'salty,spicy,sweet'},
  {'id': 5, 'name': 'salty,sour,sweet'},
  {'id': 11, 'name': 'sour,sweet'},
  {'id': 12, 'name': 'spicy'},
  {'id': 9, 'name': 'sour'},
  {'id': 13, 'name': 'spicy,sweet'}],
 [{'id': 5, 'name': 'meat,rice'},
  {'id': 0,